### LAVA2D

Lava2d is a depth-average flow model, unique in the fact that it incorporates variable temperatures efficently for quick and realistic simulations. 

### **This model is not sanctioned for forecasting work by USGS or the developers**: Do not use in those contexts!

In [1]:
import xarray as xr
import netCDF4 as nc
import matplotlib.pyplot as plt
import rasterio as rio
import cartopy.crs as ccrs
from pyproj import Transformer
import subprocess
import numpy as np

### After importing the necessary Python libraries, we must specify a DEM to use. 

Only TIFF/geotiff files are valid, and must have latitude/longitudinal georeferencing.

In [2]:
dem = "./colimafinemini.geotiff"
x = rio.open(dem)

In [3]:
bounds = x.bounds
crs = x.crs
transformer = Transformer.from_crs(crs, "EPSG:4326")
lower_left = transformer.transform(bounds.left,bounds.bottom)
upper_right = transformer.transform(bounds.right,bounds.top)
print("Your boundary coordinates, for reference, is", lower_left, ", ", upper_right, ".")

Your boundary coordinates, for reference, is (19.480044863651283, -103.65176437902552) ,  (19.520376013857597, -103.60854931216613) .


### Please specify the source coodinates of the vent

In [4]:
lon_src = -103.616

lat_src = 19.51

### Now, please set the properties of the erupting lava (at vent)

In [5]:
vent_temperature_c = 1200

viscosity_velt_vent = 100

crystal_percent = .2

### Now, we can set the consistent properties for the lava

In [6]:
liquid_density = 2700

porosity = .2

lava_specific_heat = 1500

lava_diffusivity = 5e-7

lava_conductivity = None

lava_emissivity = .95

### Below, enter rheological properties

In [7]:
phi_max_crystal_packing = .6

phi_inf_crystal_packing = .6

max_cryst_rate = .2

yield_strength_crust = 1e4

T_core_T_vent_equal = True

### Select ambient temperature values below

In [8]:
ground_temperature = 300

atm_temperature = 300

h_conv = 50

### Please enter numerical parameters

In [9]:
# Set minimum/maximum model-clock ratio =

efficiency_min = 0

efficiency_max = 10000

cfl_max = 0.5

dt_max = 5

freezable_fraction = 1.0

min_thickness = 0.1

### Set the max simulation time, and intervals to output data

In [10]:
max_time_hrs = 1

out_times = [2.5, 5, 7.5]

### Specify vent eruption timing and relative location

Please include at least two events in the array.

In [11]:
times = [0, 43200]

xy0 = [[0, 0],[0, 0]]

xy1 = [[100, -75],[100, -75]]

width = [20, 20]

discharge = [10, 10]

times = np.array(times)
xy0 = np.array(xy0)
xy1 = np.array(xy1)
width = np.array(width)
discharge = np.array(discharge)

In [12]:
inp = f"""import sim
#
#-------------------------------------------------------------------------------
sim.set_topo( # set DEM info
    path_to_dem_file    = ("{dem}"),
    Lon_SRC             = {lon_src}, # source longitude
    Lat_SRC             = {lat_src},    # source latitude
    Lon_LowerLeft       = {lower_left[1]}, # bounding box: lower-left longitude
    Lat_LowerLeft       = {lower_left[0]}, # bounding box: lower-left latitude
    Lon_UpperRight      = {upper_right[1]}, # bounding box: upper-right longitude
    Lat_UpperRight      = {upper_right[0]},   # bounding box: upper-right latitude
    fill_level          = 0.0,     # fill topography up to fill_level (m.a.s.l.)
    dx_desired          = 20.003,          # meters
    smooth_n_times      = 0
    )

sim.set_init( # set initialization type and file
    init_type = None,  # None or 'prior_model' currently supported
    init_file = None  # only specify if init_type = 'prior_model'
    )
#
#-------------------------------------------------------------------------------
sim.set_vent_props( # set lava properties @ vents
    temperature_vent_C  = {vent_temperature_c}, # deg C
    viscosity_melt_vent = {viscosity_velt_vent}, # Pa s
    cryst_vent          = {crystal_percent}  # erupted crystal fraction
    )
#
#-------------------------------------------------------------------------------
sim.set_lava_props( # set lava properties throughout
    liquid_density      = {liquid_density},   # kg m-3
    porosity            = {porosity},
    lava_specific_heat  = {lava_specific_heat},   # J kg-1 K-1
    lava_diffusivity    = {lava_diffusivity}, # m2 s-1
    lava_conductivity   = {lava_conductivity},    # W m-1 K-1
    lava_emissivity     = {lava_emissivity}
    )
#
#-------------------------------------------------------------------------------
# using Avrami n = 4
sim.set_rheo( # set rheological properties
    phi_max                 = {phi_max_crystal_packing}, # max crystal packing fraction (could be 0.6 e.g., Marsh 1981; Pinkerton and Stevenson 1992), # could be higher (Cashman et al., 1999)
    phi_inf                 = {phi_inf_crystal_packing},
    max_cryst_rate          = {max_cryst_rate}, # s-1 # max crystalization rate: max d(phi)/dt
    yield_strength_crust    = {yield_strength_crust}, # Pa
    T_core_T_vent_equal     = {T_core_T_vent_equal}  # core temperature equals vent temperature
    )
#
#-------------------------------------------------------------------------------
sim.set_ambient( # set ambient properties
    ground_temperature  = {ground_temperature}, # K
    atm_temperature     = {atm_temperature}, # K
    h_conv              = {h_conv},   # W m-2 K-1
    )
#
#-------------------------------------------------------------------------------
sim.set_numerics( # set numerical method details
    efficiency_min      = {efficiency_min}, # minmum allowable model-clock ratio
    efficiency_max      = {efficiency_max},  # maximum allowable model-clock ratio
    cfl_max             = {cfl_max},
    dt_max              = {dt_max},
    fraction_to_freeze  = {freezable_fraction},  # fraction of freezable lava per time-step
    tiny_flow           = {min_thickness},  # min thickness of lava (m)
    )
#
#-------------------------------------------------------------------------------
sim.set_runtime(
    max_iter = None, #one of them can be none, so the default value for both is none, if both none run till killed
    max_time_hr = {max_time_hrs},
    out_times = {out_times}, # hr, list of intermediate output times
    run_to_ocean = True
    )
#
#-------------------------------------------------------------------------------
sim.set_output( # where to store out.nc?
    path_out =  ('./outputs')
    )
#
#-------------------------------------------------------------------------------
sim.set_source( # set vent/fissure info: where is vent_nn.txt located?
    path_to_vent_files      = ('../example_vents')
    ) # all vent files must be named vent_01.txt, vent_02.txt, etc
#
#-------------------------------------------------------------------------------
#start simulation
sim.run()
#
#-------------------------------------------------------------------------------
#"""
f = open("../input.py","w")
f.write(inp)
f.close()

In [13]:
vents = f"""time	x0	y0	x1	y1	width	discharge"""
for time in range(len(times)):
    vents += f"""\n{times[time]}	{xy0[time,0]}	{xy0[time,1]}	{xy1[time,0]}	{xy1[time,1]}	{width[time]}	{discharge[time]}"""
# {time}	{x0}	{y0}	{x1}	{y1}	{width}	{discharge}"""
g = open("./example_vents/vent_01.txt","w")
g.write(vents)
g.close()

In [14]:
subprocess.run("python ../input.py",shell=True)

| --- Reading DEM Dataset --- |
| --- Building Modelling Subset --- |
| --- Building Coordinate Transform --- |
| --- Preparing DEM --- |
| --- DEM Preparation Complete --- |
| --- Initializing Model Domain --- |
| --- Beginning Model Evolution --- |
|  Step (sub): 10 (1)  |  dx: 20.0 m  |  Grid: 17 x 33  |  dt (type): 3.290 s (hyp)  |  t: 0.01 hr |
|  Step (sub): 20 (1)  |  dx: 20.0 m  |  Grid: 17 x 33  |  dt (type): 1.469 s (hyp)  |  t: 0.02 hr |
|  Step (sub): 30 (1)  |  dx: 20.0 m  |  Grid: 17 x 33  |  dt (type): 0.896 s (hyp)  |  t: 0.02 hr |
|  Step (sub): 40 (1)  |  dx: 20.0 m  |  Grid: 33 x 33  |  dt (type): 0.659 s (hyp)  |  t: 0.02 hr |
|  Step (sub): 50 (1)  |  dx: 20.0 m  |  Grid: 33 x 33  |  dt (type): 0.469 s (hyp)  |  t: 0.03 hr |
|  Step (sub): 60 (1)  |  dx: 20.0 m  |  Grid: 33 x 33  |  dt (type): 0.383 s (hyp)  |  t: 0.03 hr |
|  Step (sub): 70 (1)  |  dx: 20.0 m  |  Grid: 33 x 33  |  dt (type): 0.334 s (hyp)  |  t: 0.03 hr |
|  Step (sub): 80 (1)  |  dx: 20.0 m  |  G

CompletedProcess(args='python ../input.py', returncode=0)

In [15]:
a = xr.open_dataset("out.T+018.0hr.nc",group="DATA/PHYSICS")
a.lava_thickness_total.plot.imshow(cmap="hot")